In [ ]:
#! /usr/bin/env python3
#
def linpack_bench ( n, verbose = True ):

****************************************************************************80<br>
<br>
 linpack_bench() drives the LINPACK benchmark program.<br>
<br>
 Licensing:<br>
<br>
   This code is distributed under the MIT license.<br>
<br>
 Modified:<br>
<br>
   06 February 2025<br>
<br>
 Author:<br>
<br>
   Original F77 version by Jack Dongarra, Jim Bunch, Cleve Moler, Pete Stewart.<br>
   This version by John Burkardt.<br>
<br>
 Input:<br>
<br>
   integer N, the order of the matrix.<br>


In [ ]:
  from time import perf_counter
  import numpy as np
  import platform

In [ ]:
  if ( verbose ):
    print ( '' )
    print ( 'linpack_bench():' )
    print ( '  python version: ' + platform.python_version ( ) )
    print ( '  numpy version:  ' + np.version.version )
    print ( '  The LINPACK benchmark.' )
    print ( '  Datatype: float64' )
    print ( '  Matrix order N = ', n )
#
#  Set the matrix A, a solution x, and a right hand side.
#
  A = 2.0 * np.random.random ( [ n, n ] ) - 1.0
  x_exact = np.ones ( n )
  b = np.matmul ( A, x_exact )
#
#  Factor the matrix.
#
  t = perf_counter ( )
  ALU, ipvt, info = dgefa ( A, n )
  cpu = perf_counter ( ) - t

In [ ]:
  if ( info != 0 ):
    print ( '' )
    print ( 'linpack_bench(): Fatal error!' )
    print ( '  The matrix A is apparently singular.' )
    print ( '  Abnormal end of execution.' )
    raise Exception ( 'linpack_bench(): Fatal error!' )
#
#  Solve the linear system.
#
  t = perf_counter ( )
  x = dgesl ( ALU, n, ipvt, b )
  cpu = cpu + perf_counter ( ) - t
#
#  Compute the residual.
#
  r = np.matmul ( A, x ) - b
#
#  Compute infinity norms.
#
  A_norm = np.linalg.norm ( A, np.inf )
  r_norm = np.linalg.norm ( r, np.inf )
  x_norm = np.linalg.norm ( x, np.inf )
#
#  Report.
#
  eps = np.finfo(float).eps
  ratio = r_norm / A_norm / x_norm / eps

In [ ]:
  ops = ( 2 * n * n * n ) / 3.0 + 2.0 * ( n * n )
  mflops = ops / ( 1000000 * cpu )
  unit = 2.0 / mflops

In [ ]:
  cray = 0.056
  cray_ratio = cpu / cray

In [ ]:
  if ( verbose ):
    print ( "" )
    print ( "  Normalized residual = ", ratio )
    print ( "  Residual norm       = ", r_norm )
    print ( "  Machine epsilon     = ", eps )
    print ( "  First X[]           = ", x[0] )
    print ( "  Last X[]            = ", x[-1] )
    print ( "  CPU seconds         = ", cpu )
    print ( "  MegaFLOPS           = ", mflops )
    print ( "  Unit                = ", unit )
    print ( "  Cray ratio          = ", cray_ratio )
#
#  Terminate.
#
  if ( verbose ):
    print ( '' )
    print ( 'linpack_bench():' )
    print ( '  Normal end of execution.' )

In [ ]:
  return mflops

In [ ]:
def dgefa ( A, n ):

****************************************************************************80<br>
<br>
 dgefa() factors a real matrix in general storage format.<br>
<br>
 Discussion:<br>
<br>
   Gaussian elimination with partial pivoting.<br>
<br>
 Licensing:<br>
<br>
   This code is distributed under the MIT license.<br>
<br>
 Modified:<br>
<br>
   03 June 2024<br>
<br>
 Author:<br>
<br>
   Original F77 version by Jack Dongarra, Jim Bunch, Cleve Moler, Pete Stewart.<br>
   This version by John Burkardt<br>
<br>
 Reference:<br>
<br>
   Dongarra, Moler, Bunch and Stewart,<br>
   LINPACK User's Guide,<br>
   SIAM, (Society for Industrial and Applied Mathematics),<br>
   3600 University City Science Center,<br>
   Philadelphia, PA, 19104-2688.<br>
   ISBN 0-89871-172-X<br>
<br>
 Input:<br>
<br>
   real A(N,N), the matrix to be factored.<br>
<br>
   integer N, the order of the matrix A.<br>
<br>
 Output:<br>
<br>
   real ALU(N,N), an upper triangular matrix and the multipliers <br>
   used to obtain it.  The factorization can be written A=L*U, where L is <br>
   a product of permutation and unit lower triangular matrices, and U is <br>
   upper triangular.<br>
<br>
   integer IPVT(N), the pivot indices.<br>
<br>
   integer INFO, singularity indicator.<br>
   0, normal value.<br>
   K, if U(K-1,K-1) == 0.  This is not an error condition for this subroutine,<br>
   but it does indicate that DGESL or DGEDI will divide by zero if called.<br>
   Use RCOND in DGECO for a reliable indication of singularity.<br>


In [ ]:
  import numpy as np

In [ ]:
  ALU = A.copy ( )

In [ ]:
  ipvt = np.zeros ( n, dtype = int )
  info = 0

In [ ]:
  for k in range ( 0, n - 1 ):
#
#  Find L = pivot index,
#  K <= L < N,
#  index of largest entry in column K.
#
    l = -1
    amax = - np.inf
   
    for i in range ( k, n ):
      if ( amax < np.abs ( ALU[i,k] ) ):
        l = i
        amax = np.abs ( ALU[i,k] )
    ipvt[k] = l
#
#  Zero pivot implies this column already triangularized.
#
    if ( ALU[l,k] == 0.0 ):
      info = k + 1
      continue
#
#  Interchange row K and pivot row L if necessary.
#
    if ( l != k ):
      t        = ALU[l,k]
      ALU[l,k] = ALU[k,k]
      ALU[k,k] = t
#
#  Compute multipliers.
#
    ALU[k+1:n,k] = - ALU[k+1:n,k] / ALU[k,k]
#
#  Row elimination with column indexing.
#
    for j in range ( k + 1, n ):
      t = ALU[l,j]
      if ( l != k ):
        ALU[l,j] = ALU[k,j]
        ALU[k,j] = t
      ALU[k+1:n,j] = ALU[k+1:n,j] + t * ALU[k+1:n,k]

In [ ]:
  ipvt[n-1] = n - 1

In [ ]:
  if ( ALU[n-1,n-1] == 0.0 ):
    info = n

In [ ]:
  return ALU, ipvt, info

In [ ]:
def dgesl ( ALU, n, ipvt, b ):

****************************************************************************80<br>
<br>
 dgesl() solves a real general linear system A * X = B.<br>
<br>
 Discussion:<br>
<br>
   The system matrix must have been factored by DGECO or DGEFA.<br>
<br>
 Licensing:<br>
<br>
   This code is distributed under the MIT license.<br>
<br>
 Modified:<br>
<br>
   03 June 2024<br>
<br>
 Author:<br>
<br>
   Original F77 version by Jack Dongarra, Jim Bunch, Cleve Moler, Pete Stewart.<br>
   This version by John Burkardt.<br>
<br>
 Reference:<br>
<br>
   Dongarra, Moler, Bunch and Stewart,<br>
   LINPACK User's Guide,<br>
   SIAM, (Society for Industrial and Applied Mathematics),<br>
   3600 University City Science Center,<br>
   Philadelphia, PA, 19104-2688.<br>
   ISBN 0-89871-172-X<br>
<br>
 Input:<br>
<br>
   real ALU(N,N), the LU factorization from DGECO or DGEFA.<br>
<br>
   integer N, the order of the matrix A.<br>
<br>
   integer IPVT(N), the pivot vector from DGECO or DGEFA.<br>
<br>
   real B(N), the right hand side vector.<br>
<br>
 Output:<br>
<br>
   real X(N), the solution vector.<br>


In [ ]:
  import numpy as np

In [ ]:
  x = b.copy()

In [ ]:
  for k in range ( 0, n - 1 ):
    l = ipvt[k]
    t = x[l]
    if ( l != k ):
      x[l] = x[k]
      x[k] = t
    x[k+1:n] = x[k+1:n] + t * ALU[k+1:n,k]

In [ ]:
  for k in range ( n - 1, -1, -1 ):
    x[k] = x[k] / ALU[k,k]
    t = - x[k]
    x[0:k] = x[0:k] + t * ALU[0:k,k]

In [ ]:
  return x

In [ ]:
def timestamp ( ):

****************************************************************************80<br>
<br>
 timestamp() prints the date as a timestamp.<br>
<br>
 Licensing:<br>
<br>
   This code is distributed under the MIT license. <br>
<br>
 Modified:<br>
<br>
   06 April 2013<br>
<br>
 Author:<br>
<br>
   John Burkardt<br>


In [ ]:
  import time

In [ ]:
  t = time.time ( )
  print ( time.ctime ( t ) )

In [ ]:
  return

In [ ]:
if ( __name__ == '__main__' ):
  timestamp ( )
  n = 1000
  linpack_bench ( n )
  timestamp ( )